In [0]:
from pyspark.sql import Row
from pyspark import SparkConf, SparkContext, SQLContext
from pyspark.sql import SparkSession
from pyspark.sql.types import StringType
from pyspark.sql.types import FloatType
from pyspark.sql.types import DoubleType
from pyspark.sql.functions import udf
from pyspark.sql import functions as F
from pyspark.sql.functions import explode, col, udf, mean as _mean, stddev as _stddev, log, log10
from pyspark.sql.types import StructType
from pyspark.sql.types import StructField
from pyspark.sql.functions import lit

#additional imports
from pyspark.sql.functions import when 
from pyspark.sql.functions import *
from pyspark.ml.feature import StringIndexer, OneHotEncoder
from pyspark.ml.linalg import Vectors, Vector
from pyspark.ml.functions import vector_to_array

In [0]:
spark = SparkSession(sc)
sqlc=SQLContext(sc)
print(sc.getConf().getAll())

[('spark.files.useFetchCache', 'false'), ('spark.databricks.preemption.enabled', 'true'), ('spark.hadoop.fs.abfs.impl', 'shaded.databricks.v20180920_b33d810.org.apache.hadoop.fs.azurebfs.AzureBlobFileSystem'), ('spark.driver.tempDirectory', '/local_disk0/tmp'), ('spark.hadoop.fs.adl.impl.disable.cache', 'true'), ('spark.hadoop.parquet.block.size.row.check.max', '10'), ('spark.hadoop.fs.s3a.connection.maximum', '200'), ('spark.databricks.clusterUsageTags.numPerClusterInitScriptsV2', '0'), ('spark.hadoop.fs.s3a.fast.upload.active.blocks', '32'), ('spark.shuffle.reduceLocality.enabled', 'false'), ('spark.sql.streaming.checkpointFileManagerClass', 'com.databricks.spark.sql.streaming.DatabricksCheckpointFileManager'), ('spark.databricks.service.dbutils.repl.backend', 'com.databricks.dbconnect.ReplDBUtils'), ('spark.databricks.clusterUsageTags.driverNodeType', 'dev-tier-node'), ('spark.hadoop.spark.sql.sources.outputCommitterClass', 'com.databricks.backend.daemon.data.client.MapReduceDirectOutputCommitter'), ('spark.hadoop.fs.AbstractFileSystem.gs.impl', 'shaded.databricks.V2_1_4.com.google.cloud.hadoop.fs.gcs.GoogleHadoopFS'), ('spark.databricks.clusterUsageTags.instanceBootstrapType', 'ssh'), ('spark.streaming.driver.writeAheadLog.allowBatching', 'true'), ('spark.databricks.clusterSource', 'UI'), ('spark.databricks.clusterUsageTags.sparkVersion', '7.3.x-scala2.12'), ('spark.hadoop.hive.server2.transport.mode', 'http'), ('spark.hadoop.hive.server2.thrift.http.cookie.auth.enabled', 'false'), ('spark.executor.memory', '8278m'), ('spark.databricks.driverNodeTypeId', 'dev-tier-node'), ('spark.sql.parquet.compression.codec', 'snappy'), ('spark.databricks.clusterUsageTags.hailEnabled', 'false'), ('spark.databricks.clusterUsageTags.clusterLogDeliveryEnabled', 'false'), ('spark.databricks.clusterUsageTags.containerType', 'LXC'), ('spark.eventLog.enabled', 'false'), ('spark.databricks.clusterUsageTags.isIMv2Enabled', 'false'), ('spark.hadoop.databricks.s3.create.deleteUnnecessaryFakeDirectories', 'false'), ('spark.hadoop.fs.wasb.impl', 'shaded.databricks.org.apache.hadoop.fs.azure.NativeAzureFileSystem'), ('spark.executor.tempDirectory', '/local_disk0/tmp'), ('spark.r.sql.derby.temp.dir', '/tmp/RtmpU6wLkb'), ('spark.databricks.clusterUsageTags.clusterAllTags', '[{"key":"Name","value":"ce2-worker"}]'), ('spark.databricks.workerNodeTypeId', 'dev-tier-node'), ('spark.hadoop.mapred.output.committer.class', 'com.databricks.backend.daemon.data.client.DirectOutputCommitter'), ('spark.hadoop.hive.server2.thrift.http.port', '10000'), ('spark.hadoop.mapreduce.fileoutputcommitter.algorithm.version', '2'), ('spark.sql.allowMultipleContexts', 'false'), ('spark.ui.port', '43960'), ('spark.databricks.clusterUsageTags.clusterEbsVolumeSize', '0'), ('spark.hadoop.spark.driverproxy.customHeadersToProperties', 'X-Databricks-SqlGateway-SessionId:X-Databricks-SqlGateway-SessionId,X-Databricks-User-Token:spark.databricks.token,X-Databricks-Api-Url:spark.databricks.api.url,X-Databricks-ADLS-Gen1-Token:spark.databricks.adls.gen1.token,X-Databricks-ADLS-Gen2-Token:spark.databricks.adls.gen2.token,X-Databricks-AWS-Credentials:spark.databricks.aws.creds,X-Databricks-User-Id:spark.databricks.user.id,X-Databricks-User-Name:spark.databricks.user.name'), ('spark.home', '/databricks/spark'), ('spark.databricks.clusterUsageTags.clusterTargetWorkers', '0'), ('spark.sql.warehouse.dir', '/user/hive/warehouse'), ('spark.hadoop.hive.server2.idle.operation.timeout', '7200000'), ('spark.task.reaper.enabled', 'true'), ('spark.databricks.passthrough.s3a.tokenProviderClassName', 'com.databricks.backend.daemon.driver.aws.AwsCredentialContextTokenProvider'), ('spark.storage.memoryFraction', '0.5'), ('spark.databricks.session.share', 'false'), ('spark.databricks.clusterUsageTags.clusterResourceClass', 'default'), ('spark.databricks.clusterUsageTags.clusterFirstOnDemand', '0'), ('spark.driver.maxResultSize', '4g'), ('spark.app.id', 'local-1605674992493'), ('spark.databricks.delta.multiCl

In [0]:
#import table to dataframe
train_dir = '/FileStore/tables/train_data.csv'
test_dir = '/FileStore/tables/test_data.csv'

train_df = spark.read.csv(train_dir, header='true')
test_df = spark.read.csv(test_dir, header='true')
# train_df.show()
# train_df.cache()
# test_df.show()
# test_df.cache()

In [0]:
#function to show distinct values and their counts
def distinctncount(column, df):
  distinctDF = df.select(column).distinct()
  distinctDF.show()
  countDF = (df.groupBy(column).count())
  countDF.show()

In [0]:
#neo and pha are both catagorical with N and Y
#neo as shown has null values
distinctncount ('neo', train_df)
distinctncount ('pha', train_df)
distinctncount ('neo', test_df)
distinctncount ('pha', test_df)

+----+
 neo|
+----+
 Y|
 N|
null|
+----+

+----+------+
 neo| count|
+----+------+
 Y| 18369|
 N|732511|
null| 2|
+----+------+

+---+
pha|
+---+
 Y|
 N|
+---+

+---+------+
pha| count|
+---+------+
 Y| 1653|
 N|749229|
+---+------+

+----+
 neo|
+----+
 Y|
 N|
null|
+----+

+----+------+
 neo| count|
+----+------+
 Y| 4525|
 N|183194|
null| 2|
+----+------+

+---+
pha|
+---+
 Y|
 N|
+---+

+---+------+
pha| count|
+---+------+
 Y| 413|
 N|187308|
+---+------+

In [0]:
#turn null of neo into string 'N' 
train_df = train_df.withColumn('neo', when(train_df.neo.isNull(),lit('N')).otherwise(train_df.neo))
test_df = test_df.withColumn('neo', when(test_df.neo.isNull(),lit('N')).otherwise(test_df.neo))

distinctncount ('neo', train_df)
distinctncount ('neo', test_df)

+---+
neo|
+---+
 Y|
 N|
+---+

+---+------+
neo| count|
+---+------+
 Y| 18369|
 N|732513|
+---+------+

+---+
neo|
+---+
 Y|
 N|
+---+

+---+------+
neo| count|
+---+------+
 Y| 4525|
 N|183196|
+---+------+

In [0]:
#Repalce N with 0, Y with 1
train_df = train_df.withColumn('neo', regexp_replace('neo', 'N', '0'))
train_df = train_df.withColumn('neo', regexp_replace('neo', 'Y', '1'))
train_df = train_df.withColumn('pha', regexp_replace('pha', 'N', '0'))
train_df = train_df.withColumn('pha', regexp_replace('pha', 'Y', '1'))

test_df = test_df.withColumn('neo', regexp_replace('neo', 'N', '0'))
test_df = test_df.withColumn('neo', regexp_replace('neo', 'Y', '1'))
test_df = test_df.withColumn('pha', regexp_replace('pha', 'N', '0'))
test_df = test_df.withColumn('pha', regexp_replace('pha', 'Y', '1'))

distinctncount ('neo', train_df)
distinctncount ('pha', train_df)
distinctncount ('neo', test_df)
distinctncount ('pha', test_df)

+---+
neo|
+---+
 0|
 1|
+---+

+---+------+
neo| count|
+---+------+
 0|732513|
 1| 18369|
+---+------+

+---+
pha|
+---+
 0|
 1|
+---+

+---+------+
pha| count|
+---+------+
 0|749229|
 1| 1653|
+---+------+

+---+
neo|
+---+
 0|
 1|
+---+

+---+------+
neo| count|
+---+------+
 0|183196|
 1| 4525|
+---+------+

+---+
pha|
+---+
 0|
 1|
+---+

+---+------+
pha| count|
+---+------+
 0|187308|
 1| 413|
+---+------+

In [0]:
#class feature has 13 catagories, should turn into index and onehot
distinctncount ('class', train_df)
distinctncount ('class', test_df)

+-----+
class|
+-----+
 OMB|
 IEO|
 ATE|
 TJN|
 APO|
 AST|
 TNO|
 IMB|
 MCA|
 AMO|
 CEN|
 MBA|
 HYA|
+-----+

+-----+------+
class| count|
+-----+------+
 OMB| 22261|
 IEO| 20|
 ATE| 1380|
 TJN| 6531|
 APO| 10183|
 AST| 61|
 TNO| 2728|
 IMB| 15869|
 MCA| 14778|
 AMO| 6786|
 CEN| 402|
 MBA|669881|
 HYA| 2|
+-----+------+

+-----+
class|
+-----+
 OMB|
 ATE|
 TJN|
 APO|
 AST|
 TNO|
 IMB|
 MCA|
 AMO|
 CEN|
 MBA|
 HYA|
 IEO|
+-----+

+-----+------+
class| count|
+-----+------+
 OMB| 5554|
 ATE| 349|
 TJN| 1629|
 APO| 2504|
 AST| 14|
 TNO| 734|
 IMB| 4034|
 MCA| 3578|
 AMO| 1670|
 CEN| 102|
 MBA|167549|
 HYA| 2|
 IEO| 2|
+-----+------+

In [0]:
indexer = StringIndexer(inputCol = 'class', outputCol = 'class_index')
model = indexer.fit(train_df)
train_indexed = model.transform(train_df)
test_indexed = model.transform(test_df)

distinctDF = train_indexed.select('class','class_index').distinct()
distinctDF.show()
countDF = (train_indexed.groupBy('class','class_index').count())
countDF.show()

distinctDF = test_indexed.select('class','class_index').distinct()
distinctDF.show()
countDF = (test_indexed.groupBy('class','class_index').count())
countDF.show()

+-----+-----------+
class|class_index|
+-----+-----------+
 MCA| 3.0|
 CEN| 9.0|
 AMO| 5.0|
 IEO| 11.0|
 AST| 10.0|
 TNO| 7.0|
 APO| 4.0|
 TJN| 6.0|
 MBA| 0.0|
 OMB| 1.0|
 ATE| 8.0|
 IMB| 2.0|
 HYA| 12.0|
+-----+-----------+

+-----+-----------+------+
class|class_index| count|
+-----+-----------+------+
 MCA| 3.0| 14778|
 CEN| 9.0| 402|
 AMO| 5.0| 6786|
 IEO| 11.0| 20|
 AST| 10.0| 61|
 TNO| 7.0| 2728|
 APO| 4.0| 10183|
 TJN| 6.0| 6531|
 MBA| 0.0|669881|
 OMB| 1.0| 22261|
 ATE| 8.0| 1380|
 IMB| 2.0| 15869|
 HYA| 12.0| 2|
+-----+-----------+------+

+-----+-----------+
class|class_index|
+-----+-----------+
 MCA| 3.0|
 CEN| 9.0|
 AMO| 5.0|
 AST| 10.0|
 TNO| 7.0|
 APO| 4.0|
 TJN| 6.0|
 MBA| 0.0|
 OMB| 1.0|
 ATE| 8.0|
 IMB| 2.0|
 HYA| 12.0|
 IEO| 11.0|
+-----+-----------+

+-----+-----------+------+
class|class_index| count|
+-----+-----------+------+
 MCA| 3.0| 3578|
 CEN| 9.0| 102|
 AMO| 5.0| 1670|
 AST| 10.0| 14|
 TNO| 7.0| 734|
 APO| 4.0| 2504|
 TJN| 6.0| 1629|
 MBA| 0.0|167549|
 OMB| 1.0| 5554|
 ATE| 8.0| 349|
 IMB| 2.0| 4034|
 HYA| 12.0| 2|
 IEO| 11.0| 2|
+-----+-----------+------+

In [0]:
encoder = OneHotEncoder(inputCol = 'class_index', outputCol = 'class_binary')
model = encoder.fit(train_indexed)
train_encoded = model.transform(train_indexed)
test_encoded = model.transform(test_indexed)
distinctDF = train_encoded.select('class','class_index','class_binary').distinct()
distinctDF.show()
countDF = (train_encoded.groupBy('class','class_index','class_binary').count())
countDF.show()

distinctDF = test_encoded.select('class','class_index','class_binary').distinct()
distinctDF.show()
countDF = (test_encoded.groupBy('class','class_index','class_binary').count())
countDF.show()

+-----+-----------+---------------+
class|class_index| class_binary|
+-----+-----------+---------------+
 APO| 4.0| (12,[4],[1.0])|
 TNO| 7.0| (12,[7],[1.0])|
 AST| 10.0|(12,[10],[1.0])|
 ATE| 8.0| (12,[8],[1.0])|
 IEO| 11.0|(12,[11],[1.0])|
 IMB| 2.0| (12,[2],[1.0])|
 CEN| 9.0| (12,[9],[1.0])|
 MBA| 0.0| (12,[0],[1.0])|
 TJN| 6.0| (12,[6],[1.0])|
 AMO| 5.0| (12,[5],[1.0])|
 OMB| 1.0| (12,[1],[1.0])|
 MCA| 3.0| (12,[3],[1.0])|
 HYA| 12.0| (12,[],[])|
+-----+-----------+---------------+

+-----+-----------+---------------+------+
class|class_index| class_binary| count|
+-----+-----------+---------------+------+
 APO| 4.0| (12,[4],[1.0])| 10183|
 TNO| 7.0| (12,[7],[1.0])| 2728|
 AST| 10.0|(12,[10],[1.0])| 61|
 ATE| 8.0| (12,[8],[1.0])| 1380|
 IEO| 11.0|(12,[11],[1.0])| 20|
 IMB| 2.0| (12,[2],[1.0])| 15869|
 CEN| 9.0| (12,[9],[1.0])| 402|
 MBA| 0.0| (12,[0],[1.0])|669881|
 TJN| 6.0| (12,[6],[1.0])| 6531|
 AMO| 5.0| (12,[5],[1.0])| 6786|
 OMB| 1.0| (12,[1],[1.0])| 22261|
 MCA| 3.0| (12,[3],[1.0])| 14778|
 HYA| 12.0| (12,[],[])| 2|
+-----+-----------+---------------+------+

+-----+-----------+---------------+
class|class_index| class_binary|
+-----+-----------+---------------+
 APO| 4.0| (12,[4],[1.0])|
 TNO| 7.0| (12,[7],[1.0])|
 AST| 10.0|(12,[10],[1.0])|
 ATE| 8.0| (12,[8],[1.0])|
 IMB| 2.0| (12,[2],[1.0])|
 CEN| 9.0| (12,[9],[1.0])|
 MBA| 0.0| (12,[0],[1.0])|
 TJN| 6.0| (12,[6],[1.0])|
 AMO| 5.0| (12,[5],[1.0])|
 OMB| 1.0| (12,[1],[1.0])|
 MCA| 3.0| (12,[3],[1.0])|
 HYA| 12.0| (12,[],[])|
 IEO| 11.0|(12,[11],[1.0])|
+-----+-----------+---------------+

+-----+-----------+---------------+------+
class|class_index| class_binary| count|
+-----+-----------+---------------+------+
 APO| 4.0| (12,[4],[1.0])| 2504|
 TNO| 7.0| (12,[7],[1.0])| 734|
 AST| 10.0|(12,[10],[1.0])| 14|
 ATE| 8.0| (12,[8],[1.0])| 349|
 IMB| 2.0| (12,[2],[1.0])| 4034|
 CEN| 9.0| (12,[9],[1.0])| 102|
 MBA| 0.0| (12,[0],[1.0])|167549|
 TJN| 6.0| (12,[6],[1.0])| 1629|
 AMO| 5.0| (12,[5],[1.0])| 1670|
 OMB| 1.0| (12,[1],[1.0])| 5554|
 MCA| 3.0| (12,[3],[1.0])| 3578|
 HYA| 12.0| (12,[],[])| 2|
 IEO| 11.0|(12,[11],[1.0])| 2|
+-----+-----------+---------------+------+

In [0]:
#Schema change now that catagorical data are encoded
gen_notinclude = (column for column in train_encoded.columns if column not in {'class_binary'})
for column in gen_notinclude:
  train_encoded = train_encoded.withColumn(column,col(column).cast(DoubleType()))
train_encoded.printSchema()

gen_notinclude = (column for column in test_encoded.columns if column not in {'class_binary'})
for column in gen_notinclude:
   test_encoded = test_encoded.withColumn(column,col(column).cast(DoubleType()))
test_encoded.printSchema()

root
-- id: double (nullable = true)
-- spkid: double (nullable = true)
-- full_name: double (nullable = true)
-- pdes: double (nullable = true)
-- name: double (nullable = true)
-- prefix: double (nullable = true)
-- neo: double (nullable = true)
-- pha: double (nullable = true)
-- H: double (nullable = true)
-- diameter: double (nullable = true)
-- albedo: double (nullable = true)
-- diameter_sigma: double (nullable = true)
-- orbit_id: double (nullable = true)
-- epoch: double (nullable = true)
-- epoch_mjd: double (nullable = true)
-- epoch_cal: double (nullable = true)
-- equinox: double (nullable = true)
-- e: double (nullable = true)
-- a: double (nullable = true)
-- q: double (nullable = true)
-- i: double (nullable = true)
-- om: double (nullable = true)
-- w: double (nullable = true)
-- ma: double (nullable = true)
-- ad: double (nullable = true)
-- n: double (nullable = true)
-- tp: double (nullable = true)
-- tp_cal: double (nullable = true)
-- per: double (nullable = true)
-- per_y: double (nullable = true)
-- moid: double (nullable = true)
-- moid_ld: double (nullable = true)
-- sigma_e: double (nullable = true)
-- sigma_a: double (nullable = true)
-- sigma_q: double (nullable = true)
-- sigma_i: double (nullable = true)
-- sigma_om: double (nullable = true)
-- sigma_w: double (nullable = true)
-- sigma_ma: double (nullable = true)
-- sigma_ad: double (nullable = true)
-- sigma_n: double (nullable = true)
-- sigma_tp: double (nullable = true)
-- sigma_per: double (nullable = true)
-- class: double (nullable = true)
-- rms: double (nullable = true)
-- class_index: double (nullable = false)
-- class_binary: vector (nullable = true)

root
-- id: double (nullable = true)
-- spkid: double (nullable = true)
-- full_name: double (nullable = true)
-- pdes: double (nullable = true)
-- name: double (nullable = true)
-- prefix: double (nullable = true)
-- neo: double (nullable = true)
-- pha: double (nullable = true)
-- H: double (nullable = true)
-- diameter: double (nullable = true)
-- albedo: double (nullable = true)
-- diameter_sigma: double (nullable = true)
-- orbit_id: double (nullable = true)
-- epoch: double (nullable = true)
-- epoch_mjd: double (nullable = true)
-- epoch_cal: double (nullable = true)
-- equinox: double (nullable = true)
-- e: double (nullable = true)
-- a: double (nullable = true)
-- q: double (nullable = true)
-- i: double (nullable = true)
-- om: double (nullable = true)
-- w: double (nullable = true)
-- ma: double (nullable = true)
-- ad: double (nullable = true)
-- n: double (nullable = true)
-- tp: double (nullable = true)
-- tp_cal: double (nullable = true)
-- per: double (nullable = true)
-- per_y: double (nullable = true)
-- moid: double (nullable = true)
-- moid_ld: double (nullable = true)
-- sigma_e: double (nullable = true)
-- sigma_a: double (nullable = true)
-- sigma_q: double (nullable = true)
-- sigma_i: double (nullable = true)
-- sigma_om: double (nullable = true)
-- sigma_w: double (nullable = true)
-- sigma_ma: double (nullable = true)
-- sigma_ad: double (nullable = true)
-- sigma_n: double (nullable = true)
-- sigma_tp: double (nullable = true)
-- sigma_per: double (nullable = true)
-- class: double (nullable = true)
-- rms: double (nullable = true)
-- class_index: double (nullable = false)
-- class_binary: vector (nullable = true)

In [0]:
#drop remaining catagorical data
train_double = train_encoded.drop('id', 'spkid', 'full_name', 'pdes', 'name', 'prefix', 'orbit_id', 'class', 'equinox')
train_double.printSchema()

test_double = test_encoded.drop('id', 'spkid', 'full_name', 'pdes', 'name', 'prefix', 'orbit_id', 'class', 'equinox')
test_double.printSchema()

root
-- neo: double (nullable = true)
-- pha: double (nullable = true)
-- H: double (nullable = true)
-- diameter: double (nullable = true)
-- albedo: double (nullable = true)
-- diameter_sigma: double (nullable = true)
-- epoch: double (nullable = true)
-- epoch_mjd: double (nullable = true)
-- epoch_cal: double (nullable = true)
-- e: double (nullable = true)
-- a: double (nullable = true)
-- q: double (nullable = true)
-- i: double (nullable = true)
-- om: double (nullable = true)
-- w: double (nullable = true)
-- ma: double (nullable = true)
-- ad: double (nullable = true)
-- n: double (nullable = true)
-- tp: double (nullable = true)
-- tp_cal: double (nullable = true)
-- per: double (nullable = true)
-- per_y: double (nullable = true)
-- moid: double (nullable = true)
-- moid_ld: double (nullable = true)
-- sigma_e: double (nullable = true)
-- sigma_a: double (nullable = true)
-- sigma_q: double (nullable = true)
-- sigma_i: double (nullable = true)
-- sigma_om: double (nullable = true)
-- sigma_w: double (nullable = true)
-- sigma_ma: double (nullable = true)
-- sigma_ad: double (nullable = true)
-- sigma_n: double (nullable = true)
-- sigma_tp: double (nullable = true)
-- sigma_per: double (nullable = true)
-- rms: double (nullable = true)
-- class_index: double (nullable = false)
-- class_binary: vector (nullable = true)

root
-- neo: double (nullable = true)
-- pha: double (nullable = true)
-- H: double (nullable = true)
-- diameter: double (nullable = true)
-- albedo: double (nullable = true)
-- diameter_sigma: double (nullable = true)
-- epoch: double (nullable = true)
-- epoch_mjd: double (nullable = true)
-- epoch_cal: double (nullable = true)
-- e: double (nullable = true)
-- a: double (nullable = true)
-- q: double (nullable = true)
-- i: double (nullable = true)
-- om: double (nullable = true)
-- w: double (nullable = true)
-- ma: double (nullable = true)
-- ad: double (nullable = true)
-- n: double (nullable = true)
-- tp: double (nullable = true)
-- tp_cal: double (nullable = true)
-- per: double (nullable = true)
-- per_y: double (nullable = true)
-- moid: double (nullable = true)
-- moid_ld: double (nullable = true)
-- sigma_e: double (nullable = true)
-- sigma_a: double (nullable = true)
-- sigma_q: double (nullable = true)
-- sigma_i: double (nullable = true)
-- sigma_om: double (nullable = true)
-- sigma_w: double (nullable = true)
-- sigma_ma: double (nullable = true)
-- sigma_ad: double (nullable = true)
-- sigma_n: double (nullable = true)
-- sigma_tp: double (nullable = true)
-- sigma_per: double (nullable = true)
-- rms: double (nullable = true)
-- class_index: double (nullable = false)
-- class_binary: vector (nullable = true)

In [0]:
#creat list of column names with null remaining
# trainnull = []
# for column in train_double.columns:
#   if train_double.where(col(column).isNull()).count() > 0:
#     trainnull.append(column)
    
# testnull = []
# for column in test_double.columns:
#   if test_double.where(col(column).isNull()).count() > 0:
#     testnull.append(column)

In [0]:
#the query command above alone takes 7 minutes to run, here are the mannually copied results to save time
trainnull = ['H', 'diameter', 'albedo', 'diameter_sigma', 'ad', 'per', 'per_y', 'sigma_e', 'sigma_a', 'sigma_q', 'sigma_i', 'sigma_om', 'sigma_w', 'sigma_ma', 'sigma_ad', 'sigma_n', 'sigma_tp', 'sigma_per', 'rms']

testnull = ['H', 'diameter', 'albedo', 'diameter_sigma', 'ma', 'ad', 'per', 'sigma_ad', 'sigma_per']

In [0]:
#fill in remaining null with avg of repsective column
for column in trainnull:
  df_stats = train_double.select(_mean(col(column)).alias('mean')).collect()
  mean = df_stats[0]['mean']
  train_double = train_double.withColumn(column, when(col(column).isNull(),lit(mean)).otherwise(col(column)))

train_double.display()                             

neo pha H diameter albedo diameter_sigma epoch epoch_mjd epoch_cal e a q i om w ma ad n tp tp_cal per per_y moid moid_ld sigma_e sigma_a sigma_q sigma_i sigma_om sigma_w sigma_ma sigma_ad sigma_n sigma_tp sigma_per rms class_index class_binary 0.0 0.0 19.1 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.2395140902948033 2.467962162977906 1.8768504506302568 4.2847086382780155 187.4435648528415 162.4326374957067 252.60662934088057 3.0590738753255535 0.2542121643500829 2459422.955671756 2.0210727455671802E7 1416.139943265003 3.8771798583572994 0.871481 339.15426077 1.6637999999999999E-6 2.8261999999999997E-7 3.9211000000000005E-6 2.1708000000000003E-5 1.2328E-4 0.0013828 7.827999999999999E-4 3.5030999999999997E-7 4.3666E-8 0.0030714 2.4325E-4 0.54462 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 19.699 5.50656552569257 0.1305999602098697 0.47774160158044615 2457245.5 57245.0 2.0150811E7 0.2369724826300891 2.365728138761921 1.805115668491649 3.2149011772728504 58.35429368550654 290.4174436760314 345.8561643481903 2.926340609032194 0.2708674508386901 2457297.716815302 2.01510022168153E7 1329.063344027966 3.63877712259539 0.801128 311.77498376 0.0033089 0.015305000000000001 0.0056419 0.024416999999999998 0.57431 4.3121 2.1855 0.018932 0.0026285 8.4517 12.897 0.49686 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 16.4 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.2503428686832137 2.715705981368436 2.0358483554925 11.03984398082382 236.99168698795668 51.7185707883975 349.60064228534617 3.3955636072443722 0.2202317605851152 2459047.7200634778 2.02007172200635E7 1634.641611380422 4.4754048223967695 1.04054 404.9469518 4.5209000000000005E-8 4.5365E-8 1.28E-7 9.3045E-6 3.9713000000000004E-5 4.5833999999999995E-5 2.832E-5 5.6721E-8 5.518300000000001E-9 1.2943E-4 4.0959E-5 0.5393 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 19.048 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.1392587161510286 2.5278053684836403 2.17578643818893 6.0638148322223 22.79156041768309 350.82965423869337 335.73666891094086 2.8798242987783484 0.2452384858901295 2459099.4376973235 2.0200906937697303E7 1467.958826663468 4.01905222905809 1.1768 457.97525599999994 0.0011692999999999999 0.0040728000000000006 0.0064406 0.050769999999999996 0.050185 0.72613 0.29743 0.00464 5.927E-4 1.4209 3.5478 0.51993 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 17.6 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.1246940298255613 2.58183895862292 2.2598990545115965 4.448999521990394 58.92993336985667 351.3884285789563 53.224126541995325 2.9037788627342414 0.2375802577731892 2458776.4741190583 2.01910199741191E7 1515.277419825352 4.14860347659234 1.27057 494.46772689999995 1.2554E-7 4.8201E-8 3.3747E-7 1.3807999999999999E-5 7.825699999999999E-5 9.8129E-5 4.7211000000000006E-5 5.4211999999999996E-8 6.6532E-9 2.0218E-4 4.2433999999999994E-5 0.39566999999999997 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 16.7 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.1806618239919973 2.6104014333183607 2.138801549023742 15.47269809537461 96.54669521691801 327.7133701350686 166.9163030554445 3.08200131761298 0.2336916123727959 2458286.2411468015 2.0180616741146803E7 1540.491746129557 4.21763653971131 1.16784 454.4882928 5.7705E-8 3.2518E-8 1.5127E-7 6.938200000000001E-6 2.9595E-5 3.8224E-5 2.8154000000000002E-5 3.8392E-8 4.3666E-9 1.1492E-4 2.8785E-5 0.5758 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 16.2 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.2803519266124396 2.968650154672411 2.1363833643716843 1.088762837313048 210.8479264807232 164.188599159001 157.80261965459292 3.8009169449731384 0.192692824714768 2458181.5664466196 2.01803040664466E7 1868.258460235284 5.11501289592138 1.13758 442.7120086 5.2589999999999996E-8 2.2447E-8 1.6369E-7 5.3079E-6 3.8975E-4 3.900

In [0]:
for column in testnull:
  df_stats = test_double.select(_mean(col(column)).alias('mean')).collect()
  mean = df_stats[0]['mean']
  test_double = test_double.withColumn(column, when(col(column).isNull(),lit(mean)).otherwise(col(column)))
  
test_double.display()

neo pha H diameter albedo diameter_sigma epoch epoch_mjd epoch_cal e a q i om w ma ad n tp tp_cal per per_y moid moid_ld sigma_e sigma_a sigma_q sigma_i sigma_om sigma_w sigma_ma sigma_ad sigma_n sigma_tp sigma_per rms class_index class_binary 0.0 0.0 17.3 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.39470747434574105 2.637647025504356 1.5965480298519752 5.004695090879287 22.958513566461875 337.5101088922193 59.22066112957665 3.6787460211567367 0.2300801004496381 2458743.108504543 2.01909166085045E7 1564.672474049097 4.28383976467925 0.595232 231.64643744 9.492699999999999E-8 1.2808999999999999E-8 2.5372E-7 8.1749E-6 3.8829000000000004E-5 4.7473000000000004E-5 1.2115999999999999E-5 1.7864E-8 1.6759000000000002E-9 5.3733E-5 1.1397000000000001E-5 0.38528 3.0 List(0, 12, List(3), List(1.0)) 0.0 0.0 17.435 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.02445100674901471 2.91967629872945 2.8482872738442784 1.119575173823843 252.1273087617482 106.5839576931803 229.45276043438682 2.991065323614623 0.1975613646337749 2459661.2933682157 2.02203227933682E7 1822.218634029697 4.988962721504991 1.84345 717.4154365 8.5786E-8 5.6696E-8 2.6901999999999996E-7 9.4507E-6 4.2754E-4 4.6719E-4 1.8963E-4 5.8082000000000004E-8 5.754600000000001E-9 9.6511E-4 5.3077E-5 0.6791699999999999 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 18.776 5.5058838156012735 0.13073596316023076 0.48494657076804565 2455475.5 55475.0 2.0101006E7 0.2191642554913477 2.6467819059400837 2.066701920076755 3.344411492070774 80.64116355815419 311.7612798852942 347.88970824386803 3.226861891803412 0.2288900101150546 2455528.408782476 2.01011279087825E7 1572.807829485618 4.30611315396473 1.07392 417.93744639999994 0.0023279 0.020125999999999998 0.020378999999999998 0.039986 0.37189 1.8663 0.96014 0.024537 0.0026108 4.5858 17.94 0.6167699999999999 0.0 List(0, 12, List(0), List(1.0)) 1.0 0.0 22.5 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.3096638933943817 1.5803128109916817 1.0909469931589781 18.361139327382578 356.2645883781242 118.22654058452079 257.205268366673 2.069678628824386 0.49612313887158704 2459207.6960035306 2.02012241960035E7 725.6263048298981 1.98665654984229 0.20569 80.0483773 8.965700000000001E-7 2.677E-8 1.42E-6 4.8644E-5 1.2937E-5 2.5814E-4 1.4685E-4 3.5060000000000004E-8 1.2605999999999999E-8 3.0083E-4 1.8438E-5 0.58458 5.0 List(0, 12, List(5), List(1.0)) 0.0 0.0 17.660999999999998 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.1804749212675224 2.6669689271247594 2.1856479199789898 14.71333501444207 157.8498912794679 9.869375690142006 148.6862136504624 3.1482899342705286 0.2262961369475819 2458343.4573493567 2.0180812957349397E7 1590.835817420023 4.3554710949213495 1.19451 464.8674567 2.2527E-6 3.5519E-6 3.3495E-6 6.375699999999999E-5 4.595E-5 0.0023724 0.0026384 4.193E-6 4.5208E-7 0.010353 0.0031780999999999997 0.5413100000000001 0.0 List(0, 12, List(0), List(1.0)) 0.0 0.0 20.66 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.0924174389856314 1.5443905923885768 1.401661969046523 16.39801617517548 77.12056926463045 70.74379348392286 109.52484736461771 1.6871192157306318 0.5135329950220777 2458787.22286216 2.01910307228622E7 701.0260362813162 1.9193046852328999 0.47695600000000005 185.61696652 2.465E-5 4.9805E-5 7.8434E-5 0.0020685 0.0023971 0.0077039000000000005 0.039567000000000005 5.4408000000000005E-5 2.4840999999999998E-5 0.066737 0.033911000000000004 0.49827 3.0 List(0, 12, List(3), List(1.0)) 0.0 0.0 17.7 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.131410319092072 2.213022516004117 1.922208521018076 3.423528816595293 112.08976813120279 126.02034568244551 24.14609158093405 2.5038365109901584 0.2993817515997451 2458919.846815723 2.0200311346815698E7 1202.4781005400012 3.29220561407256 0.912365 

In [0]:
#Additional features "diameter_est" and "psedo_target"
train_double.select('diameter','albedo','H').show()
test_double.select('diameter','albedo','H').show()

+----------------+------------------+------+
 diameter| albedo| H|
+----------------+------------------+------+
5.50656552569257|0.1305999602098697| 19.1|
5.50656552569257|0.1305999602098697|19.699|
5.50656552569257|0.1305999602098697| 16.4|
5.50656552569257|0.1305999602098697|19.048|
5.50656552569257|0.1305999602098697| 17.6|
5.50656552569257|0.1305999602098697| 16.7|
5.50656552569257|0.1305999602098697| 16.2|
 3.72| 0.032| 16.4|
5.50656552569257|0.1305999602098697| 17.3|
5.50656552569257|0.1305999602098697| 16.8|
5.50656552569257|0.1305999602098697| 16.1|
5.50656552569257|0.1305999602098697|17.891|
5.50656552569257|0.1305999602098697| 16.7|
5.50656552569257|0.1305999602098697| 16.7|
5.50656552569257|0.1305999602098697| 17.8|
5.50656552569257|0.1305999602098697| 17.6|
5.50656552569257|0.1305999602098697|18.599|
5.50656552569257|0.1305999602098697| 17.6|
5.50656552569257|0.1305999602098697| 18.0|
5.50656552569257|0.1305999602098697| 17.9|
+----------------+------------------+------+
only showing top 20 rows

+------------------+-------------------+------------------+
 diameter| albedo| H|
+------------------+-------------------+------------------+
5.5058838156012735|0.13073596316023076| 17.3|
5.5058838156012735|0.13073596316023076| 17.435|
5.5058838156012735|0.13073596316023076| 18.776|
5.5058838156012735|0.13073596316023076| 22.5|
5.5058838156012735|0.13073596316023076|17.660999999999998|
5.5058838156012735|0.13073596316023076| 20.66|
5.5058838156012735|0.13073596316023076| 17.7|
5.5058838156012735|0.13073596316023076| 16.4|
5.5058838156012735|0.13073596316023076| 20.721|
5.5058838156012735|0.13073596316023076| 17.8|
5.5058838156012735|0.13073596316023076| 18.2|
 5.751| 0.053| 15.2|
 1.527| 0.12| 16.6|
5.5058838156012735|0.13073596316023076| 18.1|
5.5058838156012735|0.13073596316023076| 8.5|
5.5058838156012735|0.13073596316023076| 16.1|
5.5058838156012735|0.13073596316023076| 16.8|
5.5058838156012735|0.13073596316023076| 17.0|
5.5058838156012735|0.13073596316023076| 18.3|
5.5058838156012735|0.13073596316023076| 16.9|
+------------------+-------------------+------------------+
only showing top 20 rows

In [0]:
#estimated diameter based on JPL method. link: https://cneos.jpl.nasa.gov/tools/ast_size_est.html
train_new = train_double.withColumn('temp_albedo',3.1236 - (0.5 * log10(col('albedo'))))
train_new = train_new.withColumn('temp_H', 0.2 * col('H'))
train_new = train_new.withColumn('diameter_est', pow(10,(col('temp_albedo')-col('temp_H'))))
train_new.select('diameter_est').show()

test_new = test_double.withColumn('temp_albedo',3.1236 - (0.5 * log10(col('albedo'))))
test_new = test_new.withColumn('temp_H', 0.2 * col('H'))
test_new = test_new.withColumn('diameter_est', pow(10,(col('temp_albedo')-col('temp_H'))))
test_new.select('diameter_est').show()

+------------------+
 diameter_est|
+------------------+
0.5567093016648205|
0.4225017164895758|
1.9303162987688838|
0.5702016604906481|
1.1107810900044575|
1.6812352133264812|
2.1165497332598933|
 3.899644439213334|
 1.275347331178873|
1.6055671640849551|
2.2162996490659483|
0.9714679510305785|
1.6812352133264812|
1.6812352133264812|
1.0130443942356375|
1.1107810900044575|
0.7011783170559964|
1.1107810900044575|
0.9239074682916438|
0.9674498858056115|
+------------------+
only showing top 20 rows

+-------------------+
 diameter_est|
+-------------------+
 1.2746837948084113|
 1.1978500755804566|
 0.645955298041903|
0.11625254376165965|
 1.0794498358221016|
0.27127043550131946|
 1.0602358001333085|
 1.9293119958316252|
 0.2637560708948209|
 1.0125173285618134|
 0.8421752315113769|
 5.265772173624845|
 1.836577997000293|
 0.8818657273769374|
 73.3503963009242|
 2.215146555011455|
 1.6047318212865314|
 1.463532815272667|
 0.8042711022242512|
 1.5325069918813148|
+-------------------+
only showing top 20 rows

In [0]:
'''
Among NEOs, the definition of “potentially hazardous
asteroids” (PHAs) is reserved for those objects with absolute
magnitudes H  22 (i.e., diameter above ∼140 m, assuming
the average NEO albedo of 0.14 found by Mainzer et al. 2011a)
and whose minimum orbit intersection distance (MOID) is
within 0.05 au (7.5 million km) of the Earthʼs orbit.
'''

#pseudo_target based on rough classification from literature
train_new = train_new.withColumn('pseudo_target', when((col('diameter_est') >=0.13) & (col('H') <=22) & (col('moid') <= 0.05), 1).otherwise(0))
distinctDF = train_new.select('pseudo_target','pha').distinct()
distinctDF.show()
countDF = (train_new.groupBy('pseudo_target','pha').count())
countDF.show()

test_new = test_new.withColumn('pseudo_target', when((col('diameter_est') >=0.13) & (col('H') <=22) & (col('moid') <= 0.05), 1).otherwise(0))
distinctDF = test_new.select('pseudo_target','pha').distinct()
distinctDF.show()
countDF = (test_new.groupBy('pseudo_target','pha').count())
countDF.show()

+-------------+---+
pseudo_target|pha|
+-------------+---+
 1|0.0|
 0|0.0|
 1|1.0|
 0|1.0|
+-------------+---+

+-------------+---+------+
pseudo_target|pha| count|
+-------------+---+------+
 1|0.0| 31|
 0|0.0|749198|
 1|1.0| 1633|
 0|1.0| 20|
+-------------+---+------+

+-------------+---+
pseudo_target|pha|
+-------------+---+
 0|0.0|
 1|1.0|
 1|0.0|
 0|1.0|
+-------------+---+

+-------------+---+------+
pseudo_target|pha| count|
+-------------+---+------+
 0|0.0|187303|
 1|1.0| 407|
 1|0.0| 5|
 0|1.0| 6|
+-------------+---+------+

In [0]:
#drop unnecessary columns
train_new = train_new.drop(col('temp_albedo'))
train_clean_df = train_new.drop(col('temp_H'))

test_new = test_new.drop(col('temp_albedo'))
test_clean_df = test_new.drop(col('temp_H'))

In [0]:
#FINAL DF TO BE USED
train_clean_df.printSchema()
test_clean_df.printSchema()

root
-- neo: double (nullable = true)
-- pha: double (nullable = true)
-- H: double (nullable = true)
-- diameter: double (nullable = true)
-- albedo: double (nullable = true)
-- diameter_sigma: double (nullable = true)
-- epoch: double (nullable = true)
-- epoch_mjd: double (nullable = true)
-- epoch_cal: double (nullable = true)
-- e: double (nullable = true)
-- a: double (nullable = true)
-- q: double (nullable = true)
-- i: double (nullable = true)
-- om: double (nullable = true)
-- w: double (nullable = true)
-- ma: double (nullable = true)
-- ad: double (nullable = true)
-- n: double (nullable = true)
-- tp: double (nullable = true)
-- tp_cal: double (nullable = true)
-- per: double (nullable = true)
-- per_y: double (nullable = true)
-- moid: double (nullable = true)
-- moid_ld: double (nullable = true)
-- sigma_e: double (nullable = true)
-- sigma_a: double (nullable = true)
-- sigma_q: double (nullable = true)
-- sigma_i: double (nullable = true)
-- sigma_om: double (nullable = true)
-- sigma_w: double (nullable = true)
-- sigma_ma: double (nullable = true)
-- sigma_ad: double (nullable = true)
-- sigma_n: double (nullable = true)
-- sigma_tp: double (nullable = true)
-- sigma_per: double (nullable = true)
-- rms: double (nullable = true)
-- class_index: double (nullable = false)
-- class_binary: vector (nullable = true)
-- diameter_est: double (nullable = true)
-- pseudo_target: integer (nullable = false)

root
-- neo: double (nullable = true)
-- pha: double (nullable = true)
-- H: double (nullable = true)
-- diameter: double (nullable = true)
-- albedo: double (nullable = true)
-- diameter_sigma: double (nullable = true)
-- epoch: double (nullable = true)
-- epoch_mjd: double (nullable = true)
-- epoch_cal: double (nullable = true)
-- e: double (nullable = true)
-- a: double (nullable = true)
-- q: double (nullable = true)
-- i: double (nullable = true)
-- om: double (nullable = true)
-- w: double (nullable = true)
-- ma: double (nullable = true)
-- ad: double (nullable = true)
-- n: double (nullable = true)
-- tp: double (nullable = true)
-- tp_cal: double (nullable = true)
-- per: double (nullable = true)
-- per_y: double (nullable = true)
-- moid: double (nullable = true)
-- moid_ld: double (nullable = true)
-- sigma_e: double (nullable = true)
-- sigma_a: double (nullable = true)
-- sigma_q: double (nullable = true)
-- sigma_i: double (nullable = true)
-- sigma_om: double (nullable = true)
-- sigma_w: double (nullable = true)
-- sigma_ma: double (nullable = true)
-- sigma_ad: double (nullable = true)
-- sigma_n: double (nullable = true)
-- sigma_tp: double (nullable = true)
-- sigma_per: double (nullable = true)
-- rms: double (nullable = true)
-- class_index: double (nullable = false)
-- class_binary: vector (nullable = true)
-- diameter_est: double (nullable = true)
-- pseudo_target: integer (nullable = false)

In [0]:
train_clean_df.display()

neo pha H diameter albedo diameter_sigma epoch epoch_mjd epoch_cal e a q i om w ma ad n tp tp_cal per per_y moid moid_ld sigma_e sigma_a sigma_q sigma_i sigma_om sigma_w sigma_ma sigma_ad sigma_n sigma_tp sigma_per rms class_index class_binary diameter_est pseudo_target 0.0 0.0 19.1 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.2395140902948033 2.467962162977906 1.8768504506302568 4.2847086382780155 187.4435648528415 162.4326374957067 252.60662934088057 3.0590738753255535 0.2542121643500829 2459422.955671756 2.0210727455671802E7 1416.139943265003 3.8771798583572994 0.871481 339.15426077 1.6637999999999999E-6 2.8261999999999997E-7 3.9211000000000005E-6 2.1708000000000003E-5 1.2328E-4 0.0013828 7.827999999999999E-4 3.5030999999999997E-7 4.3666E-8 0.0030714 2.4325E-4 0.54462 0.0 List(0, 12, List(0), List(1.0)) 0.5567093016648205 0 0.0 0.0 19.699 5.50656552569257 0.1305999602098697 0.47774160158044615 2457245.5 57245.0 2.0150811E7 0.2369724826300891 2.365728138761921 1.805115668491649 3.2149011772728504 58.35429368550654 290.4174436760314 345.8561643481903 2.926340609032194 0.2708674508386901 2457297.716815302 2.01510022168153E7 1329.063344027966 3.63877712259539 0.801128 311.77498376 0.0033089 0.015305000000000001 0.0056419 0.024416999999999998 0.57431 4.3121 2.1855 0.018932 0.0026285 8.4517 12.897 0.49686 0.0 List(0, 12, List(0), List(1.0)) 0.4225017164895758 0 0.0 0.0 16.4 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.2503428686832137 2.715705981368436 2.0358483554925 11.03984398082382 236.99168698795668 51.7185707883975 349.60064228534617 3.3955636072443722 0.2202317605851152 2459047.7200634778 2.02007172200635E7 1634.641611380422 4.4754048223967695 1.04054 404.9469518 4.5209000000000005E-8 4.5365E-8 1.28E-7 9.3045E-6 3.9713000000000004E-5 4.5833999999999995E-5 2.832E-5 5.6721E-8 5.518300000000001E-9 1.2943E-4 4.0959E-5 0.5393 0.0 List(0, 12, List(0), List(1.0)) 1.9303162987688838 0 0.0 0.0 19.048 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.1392587161510286 2.5278053684836403 2.17578643818893 6.0638148322223 22.79156041768309 350.82965423869337 335.73666891094086 2.8798242987783484 0.2452384858901295 2459099.4376973235 2.0200906937697303E7 1467.958826663468 4.01905222905809 1.1768 457.97525599999994 0.0011692999999999999 0.0040728000000000006 0.0064406 0.050769999999999996 0.050185 0.72613 0.29743 0.00464 5.927E-4 1.4209 3.5478 0.51993 0.0 List(0, 12, List(0), List(1.0)) 0.5702016604906481 0 0.0 0.0 17.6 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.1246940298255613 2.58183895862292 2.2598990545115965 4.448999521990394 58.92993336985667 351.3884285789563 53.224126541995325 2.9037788627342414 0.2375802577731892 2458776.4741190583 2.01910199741191E7 1515.277419825352 4.14860347659234 1.27057 494.46772689999995 1.2554E-7 4.8201E-8 3.3747E-7 1.3807999999999999E-5 7.825699999999999E-5 9.8129E-5 4.7211000000000006E-5 5.4211999999999996E-8 6.6532E-9 2.0218E-4 4.2433999999999994E-5 0.39566999999999997 0.0 List(0, 12, List(0), List(1.0)) 1.1107810900044575 0 0.0 0.0 16.7 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.1806618239919973 2.6104014333183607 2.138801549023742 15.47269809537461 96.54669521691801 327.7133701350686 166.9163030554445 3.08200131761298 0.2336916123727959 2458286.2411468015 2.0180616741146803E7 1540.491746129557 4.21763653971131 1.16784 454.4882928 5.7705E-8 3.2518E-8 1.5127E-7 6.938200000000001E-6 2.9595E-5 3.8224E-5 2.8154000000000002E-5 3.8392E-8 4.3666E-9 1.1492E-4 2.8785E-5 0.5758 0.0 List(0, 12, List(0), List(1.0)) 1.6812352133264812 0 0.0 0.0 16.2 5.50656552569257 0.1305999602098697 0.47774160158044615 2459000.5 59000.0 2.0200531E7 0.2803519266124396 2.968650154672411 2.1363833643716843 1.088762837313048 210.8479264807232 164.188599159001 157.80261965459292 3.8009169449731384 0.192692824714768 2458181

In [0]:
test_clean_df.display()

neo pha H diameter albedo diameter_sigma epoch epoch_mjd epoch_cal e a q i om w ma ad n tp tp_cal per per_y moid moid_ld sigma_e sigma_a sigma_q sigma_i sigma_om sigma_w sigma_ma sigma_ad sigma_n sigma_tp sigma_per rms class_index class_binary diameter_est pseudo_target 0.0 0.0 17.3 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.39470747434574105 2.637647025504356 1.5965480298519752 5.004695090879287 22.958513566461875 337.5101088922193 59.22066112957665 3.6787460211567367 0.2300801004496381 2458743.108504543 2.01909166085045E7 1564.672474049097 4.28383976467925 0.595232 231.64643744 9.492699999999999E-8 1.2808999999999999E-8 2.5372E-7 8.1749E-6 3.8829000000000004E-5 4.7473000000000004E-5 1.2115999999999999E-5 1.7864E-8 1.6759000000000002E-9 5.3733E-5 1.1397000000000001E-5 0.38528 3.0 List(0, 12, List(3), List(1.0)) 1.2746837948084113 0 0.0 0.0 17.435 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.02445100674901471 2.91967629872945 2.8482872738442784 1.119575173823843 252.1273087617482 106.5839576931803 229.45276043438682 2.991065323614623 0.1975613646337749 2459661.2933682157 2.02203227933682E7 1822.218634029697 4.988962721504991 1.84345 717.4154365 8.5786E-8 5.6696E-8 2.6901999999999996E-7 9.4507E-6 4.2754E-4 4.6719E-4 1.8963E-4 5.8082000000000004E-8 5.754600000000001E-9 9.6511E-4 5.3077E-5 0.6791699999999999 0.0 List(0, 12, List(0), List(1.0)) 1.1978500755804566 0 0.0 0.0 18.776 5.5058838156012735 0.13073596316023076 0.48494657076804565 2455475.5 55475.0 2.0101006E7 0.2191642554913477 2.6467819059400837 2.066701920076755 3.344411492070774 80.64116355815419 311.7612798852942 347.88970824386803 3.226861891803412 0.2288900101150546 2455528.408782476 2.01011279087825E7 1572.807829485618 4.30611315396473 1.07392 417.93744639999994 0.0023279 0.020125999999999998 0.020378999999999998 0.039986 0.37189 1.8663 0.96014 0.024537 0.0026108 4.5858 17.94 0.6167699999999999 0.0 List(0, 12, List(0), List(1.0)) 0.645955298041903 0 1.0 0.0 22.5 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.3096638933943817 1.5803128109916817 1.0909469931589781 18.361139327382578 356.2645883781242 118.22654058452079 257.205268366673 2.069678628824386 0.49612313887158704 2459207.6960035306 2.02012241960035E7 725.6263048298981 1.98665654984229 0.20569 80.0483773 8.965700000000001E-7 2.677E-8 1.42E-6 4.8644E-5 1.2937E-5 2.5814E-4 1.4685E-4 3.5060000000000004E-8 1.2605999999999999E-8 3.0083E-4 1.8438E-5 0.58458 5.0 List(0, 12, List(5), List(1.0)) 0.11625254376165965 0 0.0 0.0 17.660999999999998 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.1804749212675224 2.6669689271247594 2.1856479199789898 14.71333501444207 157.8498912794679 9.869375690142006 148.6862136504624 3.1482899342705286 0.2262961369475819 2458343.4573493567 2.0180812957349397E7 1590.835817420023 4.3554710949213495 1.19451 464.8674567 2.2527E-6 3.5519E-6 3.3495E-6 6.375699999999999E-5 4.595E-5 0.0023724 0.0026384 4.193E-6 4.5208E-7 0.010353 0.0031780999999999997 0.5413100000000001 0.0 List(0, 12, List(0), List(1.0)) 1.0794498358221016 0 0.0 0.0 20.66 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.0924174389856314 1.5443905923885768 1.401661969046523 16.39801617517548 77.12056926463045 70.74379348392286 109.52484736461771 1.6871192157306318 0.5135329950220777 2458787.22286216 2.01910307228622E7 701.0260362813162 1.9193046852328999 0.47695600000000005 185.61696652 2.465E-5 4.9805E-5 7.8434E-5 0.0020685 0.0023971 0.0077039000000000005 0.039567000000000005 5.4408000000000005E-5 2.4840999999999998E-5 0.066737 0.033911000000000004 0.49827 3.0 List(0, 12, List(3), List(1.0)) 0.27127043550131946 0 0.0 0.0 17.7 5.5058838156012735 0.13073596316023076 0.48494657076804565 2459000.5 59000.0 2.0200531E7 0.131410319092072 2.213022516004117 1.922208521018076 3.423528816595293 112.08976813120279 126.0

In [0]:
# train_clean_df.write.format("orc").save("savetable/train_clean.orc")
# test_clean_df.write.format("orc").save("savetable/test_clean.orc")